In [1]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# ========== python ==========
import os
from logging import Logger
from pathlib import Path
import gc
# noinspection PyUnresolvedReferences
from typing import List, Dict, Tuple, Optional, Union, Callable, Final, Literal, get_args
import torch
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
PROJECT_DIR = Path().resolve().parents[0]
os.chdir(PROJECT_DIR)
SEED: Final = 42

In [2]:
from utils.setup import load_param, easy_logger, get_device
from utils.torch import load_model, torch_fix_seed
from torch.utils.tensorboard import SummaryWriter
from ignite.handlers import Checkpoint
from run_for_KGC import main_function
logger = easy_logger('log/test.log')

In [17]:
args = load_param('saved_models/1207/01/param.pkl')
device = get_device(device_name='cuda', logger=logger)
# args.pre_train = True
args.logger = logger
args.device = device
args.no_use_pe = False
args.max_len=512
args.tensorboard_dir=None
args.only_load_trainer_evaluator=True
args.pre_train=False
del args.optuna_file, args.device_name, args.pid
del args.study_name, args.n_trials
logger.info(args)

2022-12-07 12:46:49 - INFO - torch.py - 75 - use gpu
2022-12-07 12:46:49 - INFO - 2779003688.py - 13 - Namespace(notebook=False, train_anyway=False, logfile='saved_models/1207/01/log.log', param_file='saved_models/1207/01/param.pkl', tensorboard_dir=None, checkpoint_dir='saved_models/1207/01/checkpoint/', model_path='saved_models/1207/01/model.pth', model_version='02', resume_from_checkpoint=False, resume_from_last_point=False, only_load_trainer_evaluator=True, resume_checkpoint_path=None, console_level='info', pre_train=False, train_valid_test=True, only_train=False, use_for_challenge100=False, use_for_challenge075=False, use_title=None, do_optuna=False, story_special_num=5, relation_special_num=5, entity_special_num=5, padding_token_e=0, cls_token_e=1, mask_token_e=2, sep_token_e=3, bos_token_e=4, padding_token_r=0, cls_token_r=1, mask_token_r=2, sep_token_r=3, bos_token_r=4, padding_token_s=0, cls_token_s=1, mask_token_s=2, sep_token_s=3, bos_token_s=4, embedding_dim=128, separate_h

In [18]:
torch_fix_seed(seed=SEED)
model, data_dict = main_function(args, logger=logger)
encoder_last_layer = model.transformer.layers[-1]
model.eval()
dataset_train, dataset_valid, dataset_test = data_dict['datasets']
triple = dataset_train.triple
data_helper = data_dict['data_helper']
evaluator = data_dict['train_items']['evaluator']
load_model(model, args.model_path, device)

2022-12-07 12:46:51 - INFO - run_for_KGC.py - 723 - ----- make datahelper start. -----
2022-12-07 12:46:51 - INFO - data_helper.py - 438 - ==========Show DataHelper==========
2022-12-07 12:46:51 - INFO - data_helper.py - 439 - ==========
2022-12-07 12:46:51 - INFO - data_helper.py - 205 - ==========Show MyRawData==========
2022-12-07 12:46:51 - INFO - data_helper.py - 206 - entity_length: 7857
2022-12-07 12:46:51 - INFO - data_helper.py - 207 - relation_length: 63
2022-12-07 12:46:51 - INFO - data_helper.py - 210 - ==========Show MyRawData==========
2022-12-07 12:46:51 - INFO - data_helper.py - 441 - ==========
2022-12-07 12:46:51 - INFO - data_helper.py - 443 - entity_special_num: 5
2022-12-07 12:46:51 - INFO - data_helper.py - 444 - relation_special_num: 5
2022-12-07 12:46:51 - INFO - data_helper.py - 445 - ==========Show DataHelper==========
2022-12-07 12:46:51 - INFO - run_for_KGC.py - 725 - ----- make datahelper complete. -----
2022-12-07 12:46:51 - INFO - run_for_KGC.py - 728 - -

KgStoryTransformer02(
  (emb_entity): Embedding(7862, 128, padding_idx=0)
  (emb_relation): Embedding(68, 128, padding_idx=0)
  (pe): PositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=1028, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=1028, out_features=128, bias=True)
        (norm1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
        (activation): GELU(approximate=none)
      )
      (1): TransformerEncoderLayer(
        (self_attn): 

In [14]:
dataset_train, dataset_valid, dataset_test

(StoryTriple(padding_tensor=tensor([0, 0, 0]), sep_tensor=tensor([3, 3, 3]), triple=tensor([[   4,    4,    4],
         [ 206,   38,    5],
         [ 206,   46,    6],
         ...,
         [3432,   42,   23],
         [3432,   43, 4736],
         [3432,   49, 6828]]), bos_indices=tensor([    0,     7,    14,  ..., 13412, 13418, 13423]), max_len=512),
 StoryTripleForValid(padding_tensor=tensor([0, 0, 0]), sep_tensor=tensor([3, 3, 3]), triple=tensor([[   4,    4,    4],
         [ 206,   38,    5],
         [ 206,   21, 3651],
         ...,
         [3432,   42,   23],
         [3432,   43, 4736],
         [3432,   49, 6828]]), bos_indices=tensor([    0,     8,    15,  ..., 14686, 14692, 14698]), max_len=512, valid_filter=tensor([False, False,  True,  ..., False, False, False])),
 StoryTripleForValid(padding_tensor=tensor([0, 0, 0]), sep_tensor=tensor([3, 3, 3]), triple=tensor([[   4,    4,    4],
         [ 206,   38,    5],
         [ 206,   21, 3651],
         ...,
         [3432,

In [20]:
evaluator.run(data_helper.test_dataloader)
evaluator.state.metrics

[1/9]  11%|#1         [00:00<?]

{'loss': 13.750853326585558,
 'story_loss': 5.870057423909505,
 'relation_loss': 1.4088233841790094,
 'entity_loss': 6.4719725714789496,
 'story_accuracy': 0.03277142878867371,
 'relation_accuracy': 0.48316947618939,
 'entity_accuracy': 0.0782256286259571}

In [16]:
evaluator.run(data_helper.test_dataloader)
metrics = evaluator.state.metrics
metrics

[1/9]  11%|#1         [00:00<?]

{'loss': 13.750853114657932,
 'story_loss': 5.870057317945692,
 'relation_loss': 1.4088233047061496,
 'entity_loss': 6.471972518497044,
 'story_accuracy': 0.058760464426652066,
 'relation_accuracy': 0.6801782279096998,
 'entity_accuracy': 0.14766151904316552}

In [8]:
evaluator.run(data_helper.test_dataloader)
metrics = evaluator.state.metrics
metrics

[1/7]  14%|#4         [00:00<?]

{'loss': 13.683821950639997,
 'story_loss': 5.855381761278425,
 'relation_loss': 1.4003569228308541,
 'entity_loss': 6.428083487919399,
 'story_accuracy': 0.058760464426652066,
 'relation_accuracy': 0.6801782279096998,
 'entity_accuracy': 0.14766151904316552}

In [6]:
entities = data_helper.processed_entities
d_e = {e: i for i, e in enumerate(entities)}
relations = data_helper.processed_relations
d_r = {r: i for i, r in enumerate(relations)}
triple_df = pd.DataFrame([(entities[_t[0]], relations[_t[1]], entities[_t[2]]) for _t in triple], columns=['head', 'relation', 'tail']) 
# story_entities = triple_df
# triple_df

In [7]:
def extract(model, target, inputs):
    feature = None

    def forward_hook(module, inputs, _):
        # 順伝搬の出力を features というグローバル変数に記録する
        global features
        # 1. detach でグラフから切り離す。
        # 2. clone() でテンソルを複製する。モデルのレイヤーで ReLU(inplace=True) のように
        #    inplace で行う層があると、値がその後のレイヤーで書き換えられてまい、
        #    指定した層の出力が取得できない可能性があるため、clone() が必要。
        x, _, _ = inputs
        outputs = module.forward(x, x, x, need_weights=True)[1]
        features = outputs.detach().clone()

    # コールバック関数を登録する。
    handle = target.register_forward_hook(forward_hook)

    # 推論する
    model.eval()
    model(inputs, torch.LongTensor([[]]), torch.LongTensor([[]]), torch.LongTensor([[]]))

    # コールバック関数を解除する。
    handle.remove()

    return features

In [8]:
def heatmap_(index):
    input_ = dataset[index]
    # display([(i, entities[h], relations[r], entities[t]) for i, (h, r, t) in enumerate(input_)])
    features = extract(model, encoder_last_layer.self_attn, dataset[0][None, :])[0]
    df_atten = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_)])
    df_atten.columns=['head', 'relation', 'tail',] + [f'atten_from{i}' for i in range(len(df_atten.columns)-3)]
    display(df_atten)
    # ヒートマップの作成
    # sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
    for i in range(len(df_atten)):
        display(i, df_atten.iloc[i,:3].tolist())
        display(df_atten.sort_values(f'atten_from{i}', ascending=False).iloc[:10,:3])
        print("----------")
    plt.show()
# heatmap_(300)

In [9]:
def make_heatmap2_(input_):
    assert len(input_) == 1
    features = extract(model, encoder_last_layer.self_attn, input_)[0]
    df_atten = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_[0])])
    df_atten.columns=['head', 'relation', 'tail',] + [f'atten_from{i}' for i in range(len(df_atten.columns)-3)]
    return df_atten

In [10]:
print(f"{model.weight_head.data=}")
print(f"{model.weight_relation.data=}")
print(f"{model.weight_tail.data=}")
story_entities = triple_df['head'].tolist()
display(story_entities)

model.weight_head.data=tensor(1.3574)
model.weight_relation.data=tensor(0.3723)
model.weight_tail.data=tensor(0.5627)


['<bos_e>',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 '<bos_e>',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 '<bos_e>',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 '<bos_e>',
 'AbbeyGrange:004',
 'AbbeyGrange:004',
 'AbbeyGrange:004',
 '<bos_e>',
 'AbbeyGrange:005',
 'AbbeyGrange:005',
 'AbbeyGrange:005',
 'AbbeyGrange:005',
 '<bos_e>',
 'AbbeyGrange:006',
 'AbbeyGrange:006',
 '<bos_e>',
 'AbbeyGrange:007',
 'AbbeyGrange:007',
 'AbbeyGrange:007',
 'AbbeyGrange:007',
 '<bos_e>',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 '<bos_e>',
 'AbbeyGrange:009',
 'AbbeyGrange:009',
 '<bos_e>',
 'AbbeyGrange:009a',
 'AbbeyGrange:009a'

In [11]:
def make_ranking(_from, _to, _predicate, _whom, _subject, _why, _what, _where):
    _start_index = story_entities.index(_from)-1 
    _end_index = len(story_entities) - story_entities[::-1].index(_to)
    question_ = torch.tensor(
        [
            [d_e['<bos_e>'],d_r['<bos_r>'],d_e['<bos_e>']],
            [d_e['<mask_e>'],d_r['kgc:hasPredicate'],d_e[_predicate]],
            [d_e['<mask_e>'],d_r['kgc:whom'],d_e[_whom]],
            [d_e['<mask_e>'],d_r['kgc:subject'],d_e[_subject]],
            [d_e['<mask_e>'],d_r['kgc:why'],d_e[_why]],
            [d_e['<mask_e>'],d_r['kgc:what'],d_e[_what]],
            [d_e['<mask_e>'],d_r['kgc:where'],d_e[_where]],
        ]
    )
    mask_ = torch.tensor(
        [
            [False, False, False],
            [True, False, True],
            [True, False, True],
            [True, False, True],
            [True, False, True],
            [True, False, True],
            [True, False, True],
        ]
    )
    questions = torch.cat([triple[_start_index: _end_index], question_], dim=0).unsqueeze(0)
    masks = torch.cat([torch.zeros(_end_index-_start_index,3), mask_], dim=0).to(torch.bool).transpose(1,0).unsqueeze(0)
    tmp = []
    with torch.no_grad():
        _, (story_pred, relation_pred, entity_pred) = model(questions, masks[:,0], masks[:,1], masks[:,2])
        sorted_ = torch.argsort(entity_pred.to('cpu'), dim=1, descending=True)
        for i in range(100):
            ans_= sorted_[:, i]
            predicate_, whom_, subj_, why_, what_, where_ = ans_
            tmp.append([entities[predicate_], entities[whom_], entities[subj_], entities[why_], entities[what_], entities[where_]])
    df_ranking = pd.DataFrame(tmp, columns=['predicate', 'whom', 'subject', 'why', 'what', 'where'])
    df_attension = make_heatmap2_(questions)
    return df_ranking, df_attension

In [12]:
MASK_E = '<mask_e>'
KILL = 'word.predicate:kill'
TAKE = 'word.predicate:take'
BRING = 'word.predicate:bring'
DIE = 'word.predicate:die'
HIDE = 'word.predicate:hide'

### まだらの紐
Who killed Julia? (criminal & explanation)
被害者: Julia
犯人: Roylott
犯行に用いたもの: snake
犯行動機: 母の相続財産を独占したい

In [13]:
victim = 'SpeckledBand:Julia'
df_ranking_SpeckledBand, df_attension_SpeckledBand = make_ranking(
    'SpeckledBand:330', 'SpeckledBand:400', KILL, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_SpeckledBand.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_SpeckledBand)):
    display(i, df_attension_SpeckledBand.iloc[i,:3].tolist())
    display(df_attension_SpeckledBand.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                           whom  \
0             SpeckledBand:398           SpeckledBand:Roylott   
1            SpeckledBand:149a             SpeckledBand:snake   
2        word.predicate:wakeUp     SpeckledBand:1883-04-01T23   
3             SpeckledBand:399   DateTime:1883-04-01T23:00:00   
4              AbbeyGrange:001                AllTitle:Watson   
5             SpeckledBand:400                AbbeyGrange:001   
6             SpeckledBand:396             SpeckledBand:Helen   
7        word.predicate:return               SpeckledBand:364   
8       word.predicate:request               SpeckledBand:398   
9             SpeckledBand:395               SpeckledBand:396   
10             AbbeyGrange:010               SpeckledBand:387   
11         word.predicate:bite               SpeckledBand:397   
12       word.predicate:getOff                AllTitle:Holmes   
13        SpeckledBand:Roylott               SpeckledBand:395   
14            SpeckledBand:110                        <bos_e>   
15  SpeckledBand:1883-04-01T23            word.predicate:bite   
16            SpeckledBand:397               SpeckledBand:399   
17            SpeckledBand:387   SpeckledBand:VentilationHole   
18            SpeckledBand:364  AbbeyGrange:Lady_Brackenstall   
19            SpeckledBand:370               SpeckledBand:362   

                         subject                           why  \
0               SpeckledBand:398              SpeckledBand:397   
1               SpeckledBand:397          SpeckledBand:Roylott   
2               SpeckledBand:399                       <bos_e>   
3           SpeckledBand:Roylott              SpeckledBand:396   
4               SpeckledBand:400    SpeckledBand:1883-04-01T23   
5             SpeckledBand:snake              SpeckledBand:398   
6               SpeckledBand:396             SpeckledBand:Roma   
7             SpeckledBand:Julia            SpeckledBand:snake   
8                        <bos_e>              SpeckledBand:399   
9               SpeckledBand:395            word.predicate:hit   
10             SpeckledBand:Roma       AbbeyGrange:dining_room   
11       AbbeyGrange:dining_room              SpeckledBand:370   
12              SpeckledBand:111             SpeckledBand:safe   
13  DateTime:1883-04-01T23:00:00  DateTime:1883-04-01T23:00:00   
14               AbbeyGrange:062          word.predicate:exist   
15               AbbeyGrange:001              SpeckledBand:365   
16    SpeckledBand:1883-04-01T23              SpeckledBand:395   
17              SpeckledBand:110  SpeckledBand:VentilationHole   
18            SpeckledBand:Helen               AllTitle:Holmes   
19   SpeckledBand:sound_of_snake              SpeckledBand:400   

                               what                            where  
0                SpeckledBand:snake  SpeckledBand:mansion_of_Roylott  
1              SpeckledBand:Roylott               SpeckledBand:India  
2                  SpeckledBand:396          AbbeyGrange:dining_room  
3                 SpeckledBand:Roma                AbbeyGrange:train  
4                  SpeckledBand:395                 SpeckledBand:398  
5       SpeckledBand:metallic_sound                 SpeckledBand:396  
6                           <bos_e>                SpeckledBand:safe  
7                  SpeckledBand:398                 SpeckledBand:395  
8       SpeckledBand:sound_of_snake       SpeckledBand:1883-04-01T23  
9                  SpeckledBand:400                 SpeckledBand:399  
10               AbbeyGrange:letter                 SpeckledBand:368  
11                 SpeckledBand:397                 SpeckledBand:397  
12                SpeckledBand:safe     SpeckledBand:Julia_s_bedroom  
13  SpeckledBand:mansion_of_Roylott   SpeckledBand:garden_of_Roylott  
14                 SpeckledBand:392                 SpeckledBand:400  
15          AbbeyGrange:dining_room     DateTime:1883-04-01T23:00:00  
16                 SpeckledBand:394                 SpeckledB

0

['<bos_e>', '<bos_r>', '<bos_e>']

head          relation                          tail  \
5            <bos_e>           <bos_r>                       <bos_e>   
0            <bos_e>           <bos_r>                       <bos_e>   
11           <bos_e>           <bos_r>                       <bos_e>   
17           <bos_e>           <bos_r>                       <bos_e>   
4   SpeckledBand:330          kgc:time  DateTime:1883-04-02T03:00:00   
1   SpeckledBand:330       kgc:subject               AllTitle:Holmes   
24           <bos_e>           <bos_r>                       <bos_e>   
6   SpeckledBand:331       kgc:subject               AllTitle:Holmes   
10  SpeckledBand:331          kgc:time  DateTime:1883-04-02T03:00:00   
9   SpeckledBand:331          kgc:when    SpeckledBand:1883-04-02T03   
12  SpeckledBand:332       kgc:subject               AllTitle:Holmes   
3   SpeckledBand:330          kgc:when    SpeckledBand:1883-04-02T03   
18  SpeckledBand:333       kgc:subject               AllTitle:Holmes   
29           <bos_e>           <bos_r>                       <bos_e>   
19  SpeckledBand:333       kgc:subject               AllTitle:Watson   
13  SpeckledBand:332  kgc:hasPredicate            word.predicate:see   
14  SpeckledBand:332          kgc:what  SpeckledBand:VentilationHole   
20  SpeckledBand:333  kgc:hasPredicate           word.predicate:hear   
16  SpeckledBand:332          kgc:time  DateTime:1883-04-02T03:00:00   
15  SpeckledBand:332          kgc:when    SpeckledBand:1883-04-02T03   

    atten_from0  
5      0.091516  
0      0.087442  
11     0.062933  
17     0.041376  
4      0.038012  
1      0.035572  
24     0.023544  
6      0.022765  
10     0.019161  
9      0.018853  
12     0.018704  
3      0.017985  
18     0.017796  
29     0.014932  
19     0.013602  
13     0.011597  
14     0.011135  
20     0.011060  
16     0.010949  
15     0.010742

----------


...

----------


400

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                          tail  \
394           <bos_e>           <bos_r>                       <bos_e>   
393  SpeckledBand:400          kgc:time  DateTime:1883-04-01T23:00:00   
399          <mask_e>          kgc:what                      <mask_e>   
396          <mask_e>          kgc:whom                      <mask_e>   
397          <mask_e>       kgc:subject            SpeckledBand:Julia   
392  SpeckledBand:400          kgc:when    SpeckledBand:1883-04-01T23   
395          <mask_e>  kgc:hasPredicate           word.predicate:kill   
388           <bos_e>           <bos_r>                       <bos_e>   
400          <mask_e>         kgc:where                      <mask_e>   
386  SpeckledBand:399          kgc:when    SpeckledBand:1883-04-01T23   
391  SpeckledBand:400          kgc:what          SpeckledBand:Roylott   
387  SpeckledBand:399          kgc:time  DateTime:1883-04-01T23:00:00   
382           <bos_e>           <bos_r>                       <bos_e>   
389  SpeckledBand:400       kgc:subject            SpeckledBand:snake   
381  SpeckledBand:398          kgc:time  DateTime:1883-04-01T23:00:00   
383  SpeckledBand:399       kgc:subject            SpeckledBand:snake   
377  SpeckledBand:398       kgc:subject            SpeckledBand:snake   
390  SpeckledBand:400  kgc:hasPredicate           word.predicate:bite   
398          <mask_e>           kgc:why                      <mask_e>   
376           <bos_e>           <bos_r>                       <bos_e>   

     atten_from400  
394       0.045881  
393       0.043560  
399       0.039879  
396       0.037556  
397       0.036579  
392       0.036299  
395       0.033965  
388       0.032657  
400       0.031937  
386       0.028638  
391       0.027336  
387       0.024792  
382       0.023708  
389       0.022475  
381       0.022270  
383       0.021974  
377       0.019250  
390       0.019078  
398       0.019075  
376       0.017716

----------


### 悪魔の足跡１
Who killed the victims? (criminal & explanation)
被害者: Brenda
犯人: Mortimer
犯行動機: 財産

In [14]:
victim = 'DevilsFoot:Brenda'
df_ranking_DevilsFoot1, df_attension_DevilsFoot1 = make_ranking(
    'DevilsFoot:420', 'DevilsFoot:488', KILL, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_DevilsFoot1.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_DevilsFoot1)):
    display(i, df_attension_DevilsFoot1.iloc[i,:3].tolist())
    display(df_attension_DevilsFoot1.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate  \
0               DevilsFoot:459   
1               DevilsFoot:464   
2               DevilsFoot:437   
3         word.predicate:putOn   
4        word.predicate:direct   
5               DevilsFoot:439   
6            SpeckledBand:149a   
7               DevilsFoot:433   
8        word.predicate:return   
9               DevilsFoot:325   
10          word.predicate:put   
11  word.predicate:cannotMarry   
12              DevilsFoot:486   
13              DevilsFoot:483   
14              DevilsFoot:418   
15         word.predicate:kill   
16     word.predicate:notExist   
17          word.predicate:die   
18              DevilsFoot:482   
19              DevilsFoot:332   

                                               whom                  subject  \
0                               DevilsFoot:Mortimer           DevilsFoot:487   
1                              DevilsFoot:Sterndale           DevilsFoot:361   
2                                   DevilsFoot:Owen  word.predicate:notExist   
3                                           <bos_e>        DevilsFoot:Brenda   
4                                 DevilsFoot:Brenda      DevilsFoot:Mortimer   
5                                 DevilsFoot:George           DevilsFoot:392   
6                                   AllTitle:Holmes           DevilsFoot:420   
7                                    DevilsFoot:485           DevilsFoot:359   
8                                    DevilsFoot:484           DevilsFoot:436   
9                                DevilsFoot:Brother           DevilsFoot:272   
10                                  DevilsFoot:lamp           DevilsFoot:327   
11                                  DevilsFoot:Drug           DevilsFoot:402   
12                                   DevilsFoot:483           DevilsFoot:484   
13                                   DevilsFoot:437      ACaseOfIdentity:232   
14                                DevilsFoot:gravel           DevilsFoot:486   
15                                   DevilsFoot:438           DevilsFoot:434   
16                       DevilsFoot:Powder_medicine           DevilsFoot:260   
17                                   DevilsFoot:482           DevilsFoot:488   
18                                  AllTitle:Watson                  <bos_e>   
19  DevilsFoot:Exclusive_manager_of_shared_property           DevilsFoot:270   

                                  why                                 what  \
0           DevilsFoot:Attack_of_fear           DevilsFoot:Powder_medicine   
1                     DevilsFoot:fear                     DevilsFoot:Crazy   
2   DevilsFoot:laws_of_United_Kingdom                      DevilsFoot:fear   
3                 DevilsFoot:Cornwall         DevilsFoot:control_of_George   
4                  DevilsFoot:Visitor                       DevilsFoot:gun   
5                   DevilsFoot:regret           DevilsFoot:control_of_Owen   
6                    DevilsFoot:money    DevilsFoot:literature_of_pharmacy   
7                      DevilsFoot:269  DevilsFoot:literature_of_toxicology   
8               DevilsFoot:Negligence                      DevilsFoot:lawn   
9                      DevilsFoot:459                       DevilsFoot:482   
10        DevilsFoot:After_10_o_clock                    DevilsFoot:gravel   
11         DevilsFoot:Powder_medicine                      DevilsFoot:room   
12         DevilsFoot:Human_intention                   DevilsFoot:clothes   
13                     DevilsFoot:371              DevilsFoot:Tennis_shoes   
14                            <bos_e>                              <bos_e>   
15                     DevilsFoot:482                       DevilsFoot:434   
16      DevilsFoot:Five_minutes_later                      DevilsFoot:Drug   
17                   AbbeyGrange:dust                      DevilsFoot:lamp   
18              word.predicate:gravel                 DevilsFoot:Sterndale   
19                ResidentPatient:004                      Devils

0

['<bos_e>', '<bos_r>', '<bos_e>']

head          relation                  tail  atten_from0
5          <bos_e>           <bos_r>               <bos_e>     0.119400
0          <bos_e>           <bos_r>               <bos_e>     0.118552
10         <bos_e>           <bos_r>               <bos_e>     0.086404
6   DevilsFoot:421       kgc:subject  DevilsFoot:Sterndale     0.038616
22         <bos_e>           <bos_r>               <bos_e>     0.022313
11  DevilsFoot:422       kgc:subject   DevilsFoot:Roundhay     0.018472
3   DevilsFoot:420          kgc:what   DevilsFoot:marriage     0.018360
1   DevilsFoot:420       kgc:subject     DevilsFoot:Brenda     0.016821
2   DevilsFoot:420  kgc:hasPredicate   word.predicate:wait     0.015114
27         <bos_e>           <bos_r>               <bos_e>     0.013912
8   DevilsFoot:421          kgc:what   DevilsFoot:marriage     0.012975
23  DevilsFoot:423       kgc:subject  DevilsFoot:Sterndale     0.012780
4   DevilsFoot:420          kgc:when  DevilsFoot:long_year     0.010709
14  DevilsFoot:422          kgc:what        DevilsFoot:414     0.009638
7   DevilsFoot:421  kgc:hasPredicate   word.predicate:wait     0.009283
35  DevilsFoot:426       kgc:subject   DevilsFoot:Roundhay     0.008889
24  DevilsFoot:423       kgc:subject     DevilsFoot:Brenda     0.008363
38  DevilsFoot:426          kgc:whom  DevilsFoot:Sterndale     0.008262
31         <bos_e>           <bos_r>               <bos_e>     0.008222
13  DevilsFoot:422          kgc:what        DevilsFoot:413     0.008197

----------


...

----------


323

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
319        <mask_e>          kgc:whom   
320        <mask_e>       kgc:subject   
318        <mask_e>  kgc:hasPredicate   
322        <mask_e>          kgc:what   
314  DevilsFoot:488       kgc:subject   
311  DevilsFoot:487   kgc:hasProperty   
323        <mask_e>         kgc:where   
310  DevilsFoot:487       kgc:subject   
321        <mask_e>           kgc:why   
316  DevilsFoot:488         kgc:where   
308  DevilsFoot:486          kgc:when   
304  DevilsFoot:485          kgc:what   
298  DevilsFoot:484       kgc:subject   
302  DevilsFoot:485       kgc:subject   
300  DevilsFoot:484         kgc:where   
306  DevilsFoot:486       kgc:subject   
307  DevilsFoot:486  kgc:hasPredicate   
317         <bos_e>           <bos_r>   
303  DevilsFoot:485  kgc:hasPredicate   
315  DevilsFoot:488  kgc:hasPredicate   

                                           tail  atten_from323  
319                                    <mask_e>       0.102842  
320                           DevilsFoot:Brenda       0.072808  
318                         word.predicate:kill       0.046043  
322                                    <mask_e>       0.043216  
314                           DevilsFoot:gravel       0.040989  
311                       word.predicate:gravel       0.039519  
323                                    <mask_e>       0.038269  
310  DevilsFoot:Starting_point_of_investigation       0.037071  
321                                    <mask_e>       0.031580  
316          DevilsFoot:garden_of_pastoral_hall       0.028724  
308               DevilsFoot:Five_minutes_later       0.021943  
304                              DevilsFoot:gun       0.019617  
298                        DevilsFoot:Sterndale       0.017461  
302                        DevilsFoot:Sterndale       0.016851  
300                DevilsFoot:Outside_of_window       0.015711  
306                         DevilsFoot:Mortimer       0.013589  
307                          word.predicate:die       0.012927  
317                                     <bos_e>       0.012433  
303                         word.predicate:hold       0.012351  
315                     word.predicate:notExist       0.012090

----------


### 悪魔の足跡2
Who killed the victims? (criminal & explanation)
被害者: Mortimer
犯人: 
犯行動機: 恋人の敵

In [ ]:
victim = 'DevilsFoot:Mortimer'
df_ranking_DevilsFoot2, df_attension_DevilsFoot2 = make_ranking(
    'DevilsFoot:420', 'DevilsFoot:488', KILL, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_DevilsFoot2.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_DevilsFoot2)):
    display(i, df_attension_DevilsFoot2.iloc[i,:3].tolist())
    display(df_attension_DevilsFoot2.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate  \
0               DevilsFoot:459   
1               DevilsFoot:464   
2               DevilsFoot:437   
3            SpeckledBand:149a   
4               DevilsFoot:439   
5         word.predicate:putOn   
6        word.predicate:direct   
7               DevilsFoot:433   
8               DevilsFoot:483   
9          word.predicate:kill   
10              DevilsFoot:486   
11          word.predicate:die   
12       word.predicate:return   
13          word.predicate:put   
14  word.predicate:cannotMarry   
15              DevilsFoot:325   
16     word.predicate:notExist   
17              DevilsFoot:482   
18        word.predicate:check   
19              DevilsFoot:418   

                                               whom                  subject  \
0                               DevilsFoot:Mortimer           DevilsFoot:486   
1                              DevilsFoot:Sterndale           DevilsFoot:272   
2                                           <bos_e>      DevilsFoot:Mortimer   
3                                   AllTitle:Holmes  word.predicate:notExist   
4                                DevilsFoot:Brother           DevilsFoot:269   
5                                   DevilsFoot:Owen           DevilsFoot:488   
6                                 DevilsFoot:Brenda           DevilsFoot:402   
7                                   DevilsFoot:lamp           DevilsFoot:270   
8                                    DevilsFoot:485           DevilsFoot:487   
9                                 DevilsFoot:George           DevilsFoot:359   
10                                   DevilsFoot:484           DevilsFoot:481   
11                       DevilsFoot:Powder_medicine           DevilsFoot:399   
12                                DevilsFoot:gravel           DevilsFoot:484   
13                                   DevilsFoot:437           DevilsFoot:274   
14  DevilsFoot:Exclusive_manager_of_shared_property           DevilsFoot:482   
15                                  DevilsFoot:Drug           DevilsFoot:437   
16                                  AllTitle:Watson           DevilsFoot:260   
17                                   DevilsFoot:483           DevilsFoot:403   
18                           ACaseOfIdentity:Hosmer           DevilsFoot:265   
19                                   DevilsFoot:438       word.predicate:die   

                                  why                                 what  \
0           DevilsFoot:Attack_of_fear           DevilsFoot:Powder_medicine   
1                     DevilsFoot:fear                     DevilsFoot:Crazy   
2   DevilsFoot:laws_of_United_Kingdom                      DevilsFoot:fear   
3                   DevilsFoot:regret                       DevilsFoot:gun   
4                    DevilsFoot:money         DevilsFoot:control_of_George   
5                  DevilsFoot:Visitor                   DevilsFoot:clothes   
6                 DevilsFoot:Cornwall           DevilsFoot:control_of_Owen   
7                      DevilsFoot:269    DevilsFoot:literature_of_pharmacy   
8                      DevilsFoot:459                      DevilsFoot:lawn   
9          DevilsFoot:Powder_medicine  DevilsFoot:literature_of_toxicology   
10        DevilsFoot:After_10_o_clock                    DevilsFoot:gravel   
11                            <bos_e>                              <bos_e>   
12              DevilsFoot:Negligence              DevilsFoot:Tennis_shoes   
13                     DevilsFoot:371                       DevilsFoot:458   
14      DevilsFoot:Five_minutes_later                       DevilsFoot:434   
15         DevilsFoot:Human_intention              DevilsFoot:Good_friends   
16                ResidentPatient:004                       DevilsFoot:482   
17              word.predicate:gravel                      DevilsFoot:room   
18                     DevilsFoot:482                  DevilsFoot:Mortimer   
19            word.predicate:notExist    DevilsFoot:Another_inter

0

['<bos_e>', '<bos_r>', '<bos_e>']

head          relation                  tail  atten_from0
5          <bos_e>           <bos_r>               <bos_e>     0.119578
0          <bos_e>           <bos_r>               <bos_e>     0.118845
10         <bos_e>           <bos_r>               <bos_e>     0.086531
6   DevilsFoot:421       kgc:subject  DevilsFoot:Sterndale     0.038542
22         <bos_e>           <bos_r>               <bos_e>     0.022273
11  DevilsFoot:422       kgc:subject   DevilsFoot:Roundhay     0.018424
3   DevilsFoot:420          kgc:what   DevilsFoot:marriage     0.018383
1   DevilsFoot:420       kgc:subject     DevilsFoot:Brenda     0.016781
2   DevilsFoot:420  kgc:hasPredicate   word.predicate:wait     0.015142
27         <bos_e>           <bos_r>               <bos_e>     0.013876
8   DevilsFoot:421          kgc:what   DevilsFoot:marriage     0.012960
23  DevilsFoot:423       kgc:subject  DevilsFoot:Sterndale     0.012737
4   DevilsFoot:420          kgc:when  DevilsFoot:long_year     0.010731
14  DevilsFoot:422          kgc:what        DevilsFoot:414     0.009628
7   DevilsFoot:421  kgc:hasPredicate   word.predicate:wait     0.009279
35  DevilsFoot:426       kgc:subject   DevilsFoot:Roundhay     0.008861
24  DevilsFoot:423       kgc:subject     DevilsFoot:Brenda     0.008347
38  DevilsFoot:426          kgc:whom  DevilsFoot:Sterndale     0.008229
31         <bos_e>           <bos_r>               <bos_e>     0.008196
13  DevilsFoot:422          kgc:what        DevilsFoot:413     0.008186

----------


...

['DevilsFoot:473', 'kgc:hasPredicate', 'word.predicate:say']

head         relation                             tail  \
257  DevilsFoot:473         kgc:what                   DevilsFoot:484   
247  DevilsFoot:473         kgc:what                   DevilsFoot:474   
253  DevilsFoot:473         kgc:what                   DevilsFoot:480   
251  DevilsFoot:473         kgc:what                   DevilsFoot:478   
256  DevilsFoot:473         kgc:what                   DevilsFoot:483   
252  DevilsFoot:473         kgc:what                   DevilsFoot:479   
258  DevilsFoot:473         kgc:what                   DevilsFoot:485   
249  DevilsFoot:473         kgc:what                   DevilsFoot:476   
261  DevilsFoot:474      kgc:subject             DevilsFoot:Sterndale   
259  DevilsFoot:473         kgc:what                   DevilsFoot:486   
254  DevilsFoot:473         kgc:what                   DevilsFoot:481   
248  DevilsFoot:473         kgc:what                   DevilsFoot:475   
242  DevilsFoot:472         kgc:what     DevilsFoot:guilt_of_Mortimer   
255  DevilsFoot:473         kgc:what                   DevilsFoot:482   
237  DevilsFoot:471         kgc:what  DevilsFoot:same_fate_of__George   
250  DevilsFoot:473         kgc:what                   DevilsFoot:477   
240  DevilsFoot:472      kgc:subject             DevilsFoot:Sterndale   
265  DevilsFoot:475  kgc:hasProperty       word.predicate:Executioner   
232  DevilsFoot:470         kgc:what                   DevilsFoot:471   
245  DevilsFoot:473      kgc:subject             DevilsFoot:Sterndale   

     atten_from246  
257       0.037264  
247       0.036372  
253       0.035328  
251       0.033706  
256       0.031549  
252       0.028504  
258       0.028464  
249       0.027420  
261       0.027318  
259       0.026842  
254       0.026222  
248       0.025618  
242       0.024729  
255       0.023456  
237       0.023003  
250       0.022776  
240       0.021698  
265       0.020039  
232       0.019332  
245       0.018525

----------


247

['DevilsFoot:473', 'kgc:what', 'DevilsFoot:474']

### 背中の曲がった男: 
Why did Barclay die?
被害者: Barclay
犯人: 
犯行動機: 

In [ ]:
victim = 'CrookedMan:Barclay'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    'CrookedMan:300', 'CrookedMan:372', DIE, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_CrookedMan)):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

### 僧坊荘園
Who killed Lord Blackenstall? (criminal & explanation)
被害者: Sir_Eustace_Brackenstall
犯人: 
犯行動機: 

In [ ]:
victim = 'AbbeyGrange:Sir_Eustace_Brackenstall'
df_ranking_AbbeyGrange, df_attension_AbbeyGrange = make_ranking(
    'AbbeyGrange:350', 'AbbeyGrange:413', KILL, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_AbbeyGrange.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_AbbeyGrange)):
    display(i, df_attension_AbbeyGrange.iloc[i,:3].tolist())
    display(df_attension_AbbeyGrange.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

### 入院患者
Who killed Blessington? (criminal & explanation)
被害者: Blessington
犯人: 3人
犯行動機: 

In [ ]:
victim = 'ResidentPatient:Blessington'
df_ranking_Blessington, df_attension_Blessington = make_ranking(
    'ResidentPatient:250', 'ResidentPatient:323', KILL, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_Blessington.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_Blessington)):
    display(i, df_attension_Blessington.iloc[i,:3].tolist())
    display(df_attension_Blessington.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

### 白銀
Who took out the White Silver Blaze? (criminal & explanation) 
被害者: Silver_Blaze
犯人: 
犯行動機: 

In [ ]:
victim = 'SilverBlaze:Silver_Blaze'
df_ranking_SilverBlaze, df_attension_SilverBlaze = make_ranking(
    'SilverBlaze:330', 'SilverBlaze:396', TAKE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_SilverBlaze.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_SilverBlaze)):
    display(i, df_attension_SilverBlaze.iloc[i,:3].tolist())
    display(df_attension_SilverBlaze.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

### 花嫁失踪事件（同一事件）
hozmaの失踪の名瀬を探る
被害者: Silver_Blaze
犯人: 
犯行動機: 

In [ ]:
"""
victim = 'ACaseOfIdentity:Silver_Blaze'
df_ranking_SpeckledBand, df_attension_SpeckledBand = make_ranking(
    'SilverBlaze:182', 'SilverBlaze:244', HIDE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_SpeckledBand.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
for i in range(len(df_attension_SpeckledBand)):
    display(i, df_attension_SpeckledBand.iloc[i,:3].tolist())
    display(df_attension_SpeckledBand.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")
"""